# Task 2. Detoxification through ruPROMPTs and metric hacking
## Yurchenko Vladislav
## @moomin_dad
<img src="img/dad.png" width="75" >

## Technical Report


Мои эксперименты:

| Checkpoint | Additional info | Joint score | Leaderbord |
| :- | :- | -: | -: |
| baseline |  | - | 0.36  |
| baseline (prev t5) |  | - | 0.45  |
| ruPrompts | - | 0.7274969536 | 0.66 |
| openAI zeroPrompt | - | 0.3600979288 | - |


In [1]:
%pip install ruprompts 

Note: you may need to restart the kernel to use updated packages.


# ruPROMPTs tutorial

This [tutorial](https://github.com/ai-forever/ru-prompts/blob/main/notebooks/detox-russe-train-python.ipynb) presents an exaple of prompt-tuning with ruPROMTS framework for the detoxification task.

In [1]:
!wget -O task2/train.csv https://raw.githubusercontent.com/skoltech-nlp/russe_detox_2022/main/data/input/train.tsv
!wget -O task2/dev.csv https://raw.githubusercontent.com/skoltech-nlp/russe_detox_2022/main/data/input/dev.tsv
!wget -O task2/test.csv https://raw.githubusercontent.com/skoltech-nlp/russe_detox_2022/main/data/input/test.tsv

--2023-04-10 23:54:59--  https://raw.githubusercontent.com/skoltech-nlp/russe_detox_2022/main/data/input/train.tsv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.110.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1902888 (1.8M) [text/plain]
Saving to: ‘task2/train.csv’

task2/train.csv     100%[===================>]   1.81M  8.28MB/s    in 0.2s    

2023-04-10 23:55:00 (8.28 MB/s) - ‘task2/train.csv’ saved [1902888/1902888]

--2023-04-10 23:55:00--  https://raw.githubusercontent.com/skoltech-nlp/russe_detox_2022/main/data/input/dev.tsv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.110.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Leng

In [2]:
import pandas as pd

df = pd.read_csv("task2/train.tsv", sep="\t")
df.drop(["index"], axis=1, inplace=True)
df.to_csv("task2/train.tsv", index=False, sep="\t")

KeyError: "['index'] not found in axis"

## Training

In [2]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

Load the dataset:

In [5]:
!pip install datasets

In [1]:
from datasets import load_dataset

datasets = load_dataset("csv", data_files={
    "train": "task2/train.tsv", 
    "validation": "task2/dev.tsv",
}, sep="\t")
train_dataset = datasets["train"]
valid_dataset = datasets["validation"]

Found cached dataset csv (/home/jovyan/.cache/huggingface/datasets/csv/default-6f14a3b9c6758b34/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317)


  0%|          | 0/2 [00:00<?, ?it/s]

Load the backbone:

In [3]:
from transformers import GPT2LMHeadModel, AutoTokenizer

backbone_id = "sberbank-ai/rugpt3large_based_on_gpt2"

model = GPT2LMHeadModel.from_pretrained(backbone_id)
tokenizer = AutoTokenizer.from_pretrained(backbone_id, pad_token="<pad>", eos_token="<pad>")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Define the prompt format:

In [4]:
from ruprompts import PromptFormat

prompt_format = PromptFormat("<P*100>{toxic_comment}<P*20>")

Define the parametrization of trainable embeddings:

In [5]:
from ruprompts import TensorPromptProvider
from transformers import set_seed

set_seed(1)

prompt_provider = TensorPromptProvider()

Compose prompt format and prompt provider into prompt object and apply it to the model and tokenizer, i.e. add special tokens to the tokenizer and modify the layer of input embeddings of the model:

In [6]:
from ruprompts import Prompt

prompt = Prompt(prompt_format, prompt_provider)
prompt.patch(model, tokenizer)

Preprocess the data:
1. format the data entries with the specified prompt format
2. tokenize the resulting sequences
3. truncate the `truncation_field` if sequence length exceeds `max_tokens`

In [7]:
from ruprompts import Text2TextPreprocessor

preprocessor = Text2TextPreprocessor(
    prompt_format=prompt_format,
    tokenizer=tokenizer,
    target_field="neutral_comment1",
    max_tokens=1792,
    truncation_field="toxic_comment",
)

train_dataset = train_dataset.map(preprocessor)
valid_dataset = valid_dataset.map(preprocessor)

Loading cached processed dataset at /home/jovyan/.cache/huggingface/datasets/csv/default-6f14a3b9c6758b34/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-2f6b0322d76cd568.arrow
Loading cached processed dataset at /home/jovyan/.cache/huggingface/datasets/csv/default-6f14a3b9c6758b34/0.0.0/6b34fb8fcf56f7c8ba51dc895bfa2bfbe43546f190a60fcf74bb5e8afdcc2317/cache-0b69788a14bad05d.arrow


Define training arguments:

In [8]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir=".",
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    gradient_accumulation_steps=1,
    eval_steps=1000,
    save_steps=1000,
    logging_steps=100,
    evaluation_strategy="steps",
    save_strategy="steps",
    logging_strategy="steps",
    save_total_limit=2,
    metric_for_best_model="eval_loss",
    learning_rate=0.1,
    max_steps=100000,
    report_to="tensorboard",
    # report_to=["tensorboard", "wandb"],  # uncomment to log to WandB
    logging_dir="logs",
    seed=1,
)

Choose optimization options:

In [9]:
from transformers.optimization import AdamW, get_linear_schedule_with_warmup

optimizer = AdamW(prompt_provider.parameters(), lr=training_args.learning_rate)
scheduler = get_linear_schedule_with_warmup(
    optimizer,
    num_warmup_steps=2000,
    num_training_steps=training_args.max_steps,
)

/home/jovyan/.imgenv-jupyter-server-dfcbc5cc9913-0/lib/python3.7/site-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


Define the callbacks and start training:

In [10]:
from transformers import Trainer
from ruprompts.callbacks import (
    FreezeTransformerUnfreezePrompt,
    ReduceCheckpoint,
    SavePretrainedPrompt,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=valid_dataset,
    data_collator=preprocessor.collate_fn(),
    optimizers=(optimizer, scheduler),
    callbacks=[FreezeTransformerUnfreezePrompt(), ReduceCheckpoint(), SavePretrainedPrompt(prompt)],
)

trainer.train()

max_steps is given, it will override any value given in num_train_epochs
The following columns in the training set don't have a corresponding argument in `GPT2LMHeadModel.forward` and have been ignored: neutral_comment3, neutral_comment2, neutral_comment1, toxic_comment. If neutral_comment3, neutral_comment2, neutral_comment1, toxic_comment are not expected by `GPT2LMHeadModel.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 6948
  Num Epochs = 29
  Instantaneous batch size per device = 2
  Total train batch size (w. parallel, distributed & accumulation) = 2
  Gradient Accumulation steps = 1
  Total optimization steps = 100000
  Number of trainable parameters = 760484352
You're using a GPT2TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


KeyboardInterrupt: 

In [11]:
!nvidia-smi

Tue Apr 11 00:35:19 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.172.01   Driver Version: 450.172.01   CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  A100-PCIE-40GB      On   | 00000000:CA:00.0 Off |                    0 |
| N/A   32C    P0    39W / 250W |  35258MiB / 40537MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

## Inference

Load prompt from the last checkpoint:

In [12]:
from transformers import pipeline

prompt = Prompt.from_pretrained(f"./checkpoint-{training_args.max_steps}")

ppln = pipeline("text2text-generation-with-prompt", prompt=prompt, model=model, tokenizer=tokenizer, device=0)

In [13]:
query = "Ублюдок, мать твою, а ну иди сюда"
options = ppln({"toxic_comment": query}, 
            do_sample=False,           
            num_beams=10,
            num_return_sequences=10
              )
options

Generate config GenerationConfig {
  "bos_token_id": 50256,
  "eos_token_id": 50256,
  "transformers_version": "4.26.1"
}

Setting `pad_token_id` to `eos_token_id`:0 for open-end generation.


[{'generated_text': 'А ну иди сюда'},
 {'generated_text': 'а ну иди сюда'},
 {'generated_text': 'А ну пошли сюда'},
 {'generated_text': 'а ну давай сюда'},
 {'generated_text': 'А ну иди сюда.'},
 {'generated_text': 'А ну пошел сюда'},
 {'generated_text': 'А ну давай сюда'},
 {'generated_text': 'А ну подойди сюда'},
 {'generated_text': 'А ну, иди сюда'},
 {'generated_text': 'Отстань от меня'}]

In [14]:
use_cuda = True

from ru_detoxification_evaluation import load_model
from ru_detoxification_metrics import evaluate_style

from transformers import AutoTokenizer, AutoModelForSequenceClassification, AutoModel
from ru_detoxification_metrics import evaluate_cosine_similarity
from ru_detoxification_metrics import evaluate_cola_relative

style_model, style_tokenizer = load_model('SkolkovoInstitute/russian_toxicity_classifier', use_cuda=use_cuda)

accuracy = evaluate_style(
    model = style_model,
    tokenizer = style_tokenizer,
    texts = [query],
    target_label=0,  # 1 is toxic, 0 is neutral
    batch_size=32, 
    verbose=True
)
accuracy

loading configuration file config.json from cache at /home/jovyan/.cache/huggingface/hub/models--SkolkovoInstitute--russian_toxicity_classifier/snapshots/92d6598d6c9d2beab7cd7f27013f3fe1bb0c9b39/config.json
Model config BertConfig {
  "_name_or_path": "SkolkovoInstitute/russian_toxicity_classifier",
  "architectures": [
    "BertForSequenceClassification"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "neutral",
    "1": "toxic"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "label2id": {
    "neutral": 0,
    "toxic": 1
  },
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "output_past": true,
  "pad_token_id": 0,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 12,
  "pooler_num

  0%|          | 0/1 [00:00<?, ?it/s]

array([0.10729373], dtype=float32)

In [15]:
meaning_model, meaning_tokenizer = load_model('cointegrated/LaBSE-en-ru', use_cuda=use_cuda, model_class=AutoModel)
similarity = evaluate_cosine_similarity(
    model = meaning_model,
    tokenizer = meaning_tokenizer,
    original_texts = [query],
    rewritten_texts = [options[0]['generated_text']],
    batch_size=32,
    verbose=True,
    )
similarity

loading configuration file config.json from cache at /home/jovyan/.cache/huggingface/hub/models--cointegrated--LaBSE-en-ru/snapshots/54c1434596262eb6396e1676f8684bae0abb3be1/config.json
Model config BertConfig {
  "_name_or_path": "cointegrated/LaBSE-en-ru",
  "architectures": [
    "BertForPreTraining"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 12,
  "pooler_num_fc_layers": 3,
  "pooler_size_per_head": 128,
  "pooler_type": "first_token_transform",
  "position_embedding_type": "absolute",
  "transformers_version": "4.26.1",
  "type_vocab_size": 2

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

array([0.42332578], dtype=float32)

In [17]:
cola_model, cola_tolenizer = load_model('SkolkovoInstitute/rubert-base-corruption-detector', use_cuda=use_cuda)
fluency = evaluate_cola_relative(
    model = cola_model,
    tokenizer = cola_tolenizer,
    original_texts = [query],
    rewritten_texts = [options[0]['generated_text']],
    target_label=1,
    batch_size=32,
    verbose=True
)
fluency

loading configuration file config.json from cache at /home/jovyan/.cache/huggingface/hub/models--SkolkovoInstitute--rubert-base-corruption-detector/snapshots/27965caf27a4897bd0df76128dc8707ca7e212a7/config.json
Model config BertConfig {
  "_name_or_path": "SkolkovoInstitute/rubert-base-corruption-detector",
  "architectures": [
    "BertForSequenceClassification"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "unnatural",
    "1": "natural"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "label2id": {
    "natural": 1,
    "unnatural": 0
  },
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "output_past": true,
  "pad_token_id": 0,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 1

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

array([0.9671553], dtype=float32)

In [18]:
joint = accuracy * similarity * fluency
joint

array([0.04392838], dtype=float32)

In [19]:
from nltk.translate.chrf_score import corpus_chrf

def calc_score(toxic_text, prediction):
    accuracy = evaluate_style(
    model = style_model,
    tokenizer = style_tokenizer,
    texts = [prediction],
    target_label=0,  # 1 is toxic, 0 is neutral
    batch_size=32, 
    verbose=True
    )
    
    similarity = evaluate_cosine_similarity(
    model = meaning_model,
    tokenizer = meaning_tokenizer,
    original_texts = [toxic_text],
    rewritten_texts = [prediction],
    batch_size=32,
    verbose=True,
    )
    
    fluency = evaluate_cola_relative(
    model = cola_model,
    tokenizer = cola_tolenizer,
    original_texts = [toxic_text],
    rewritten_texts = [prediction],
    target_label=1,
    batch_size=32,
    verbose=True
    )
    
    return accuracy * similarity * fluency
    
calc_score(query, options[3]['generated_text'])

# а это хитрое расстояние от нейтрального текста (в тестовой выборке) к переписанному, как его тут учесть?
corpus_chrf(neutral_references, rewritten)

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

array([0.33618984], dtype=float32)

Run inference:

In [53]:
from tqdm import tqdm
import transformers
import numpy as np

transformers.logging.set_verbosity_error()

beam_count = 10

predictions = []

with open("task2/subm.txt", "w") as f:
    for query in tqdm(valid_dataset["toxic_comment"]):
        options = ppln(
            {"toxic_comment": query},
            do_sample=False,
            num_beams=beam_count,
            num_return_sequences=beam_count,
        )

        options = [opt["generated_text"].replace("<pad>", "") for opt in options]
        scores  = [calc_score(query, opt) for opt in options]
        answer = options[np.argmax(scores)]
        predictions.append(answer)
        f.write(answer.replace("\n", "") + "\n")

  0%|          | 0/800 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  3%|▎         | 24/800 [00:36<19:26,  1.50s/it]


KeyboardInterrupt: 

In [ ]:
from tqdm import tqdm
import transformers
import numpy as np

transformers.logging.set_verbosity_error()

beam_count = 10 

predictions = []

with open("task2/test.tsv", "r") as test_f:
    with open("task2/test_submission.txt", "w") as f:
        for line in test_f:
            query = line.strip("\r\n")
            options = ppln(
                {"toxic_comment": query},
                do_sample=False,
                num_beams=beam_count,
                num_return_sequences=beam_count,
            )

            options = [opt["generated_text"].replace("<pad>", "") for opt in options]
            scores  = [calc_score(query, opt) for opt in options]
            answer = options[np.argmax(scores)]
            predictions.append(answer)
            f.write(answer.replace("\n", "") + "\n")

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

# OpenAI interface

In [1]:
!pip install openai

In [1]:
import os
import openai
openai.api_key = "XXX"

In [2]:
def rewrite_open_ai(text):
    query = f"Переформулируй текст без вульгарных выражений: {text}"
    response = openai.ChatCompletion.create(
      model="gpt-3.5-turbo",
        messages=[
        {"role": "user", "content": query}
      ] ,
      # prompt=query,
      temperature=0,
      max_tokens=500,
      top_p=1.0,
      frequency_penalty=0.0,
      presence_penalty=0.0,
      stop=["\n"]
    )
    return response['choices'][0]['message']['content']

rewrite_open_ai("какой дебил эту придумывает ")

'Кто же придумывает такое глупое?'

In [3]:
import time
time.sleep(0.5)

In [4]:
with open("task2/test.tsv", "r") as test_f:
    with open("task2/test_open_ai_submission.txt", "w") as f:
        for idx, line in enumerate(test_f):
            if idx < 718:
                continue
            answer = rewrite_open_ai(line.strip("\r\n"))
            time.sleep(0.5)
            print(idx, '-> ', line.strip("\r\n"), ' -> ', answer)
            f.write(answer.replace("\n", "") + "\n")

718 ->  Я вот хуйню бы творить не стал и если надо, то изменился бы ради общественного блага  ->  Я не совершал бы неправильных поступков и готов измениться, если это принесет пользу обществу.
719 ->  Просто либо воруют либо жопу свою поднять не могут в лице директора чтобы выбить нормальные условия.  ->  Либо они крадут, либо не могут добиться улучшения условий работы у директора.
720 ->  У Батикова тоже клоунады хватает, впрочем  ->  У Батикова также есть свои шутки, однако.
721 ->  склонен ко всем формам наркозависимости, сучара, а также к религиозному фанатизму, что по сути одно и то же  ->  Человек склонен к различным формам зависимости, включая наркотики, и проявляет фанатизм в религиозных убеждениях, что схоже между собой.
722 ->  Сами превращаете интернет в помойку, сами же за это и получаете.  ->  Вы сами захламляете интернет, и сами же несете за это ответственность.
723 ->  вот они сволочи и долетались  ->  Вот они негодяи и получили заслуженное.
724 ->  судя по словесному по